In [1]:
import numpy as np
import matplotlib.pyplot as plt

In [2]:
import os

# Apuntar EXPLÍCITAMENTE a la licencia (OneDrive)
os.environ["GRB_LICENSE_FILE"] = r"C:\Users\PC2\OneDrive\Desktop\gurobi.lic"

print("GRB_LICENSE_FILE =", os.environ["GRB_LICENSE_FILE"])

GRB_LICENSE_FILE = C:\Users\PC2\OneDrive\Desktop\gurobi.lic


In [3]:
import gurobipy as gp
print("Gurobi version:", gp.gurobi.version())

Gurobi version: (13, 0, 0)


## Foward problem y generacion de D



In [4]:
from gurobipy import GRB


def solve_original_lp(c, A, b, output=0):
    m = gp.Model("original_lp")
    m.Params.OutputFlag = output

    n = len(c)
    m_con = len(b)

    x = m.addVars(n, lb=0.0, name="x")
    m.setObjective(gp.quicksum(c[j] * x[j] for j in range(n)), GRB.MINIMIZE)

    for i in range(m_con):
        m.addConstr(gp.quicksum(A[i][j] * x[j] for j in range(n)) >= b[i], name=f"con_{i}")

    m.optimize()
    if m.Status != GRB.OPTIMAL:
        raise RuntimeError(f"Original LP not optimal. Status={m.Status}")

    x_hat = [x[j].X for j in range(n)]
    z_hat = m.ObjVal
    return x_hat, z_hat

In [5]:

def apply_favorable_property(modelF, xF, property_list, other_params=None):
    """
    Simplified context:
      - xF is a 1D gurobi variable container: xF[j] for j = 0..n-1
      - property_list is a list of dicts describing linear properties on x
      - other_params can contain x_hat, n, etc. if needed

    Supported property types (examples):
      - {"type":"x_ge", "idx":0, "rhs":2.0}
      - {"type":"x_le", "idx":1, "rhs":3.5}
      - {"type":"sum_ge", "idxs":[0,1], "rhs":7.0}
      - {"type":"sum_le", "idxs":[0,1], "rhs":10.0}
      - {"type":"custom", "expr": lambda m,x,params: ... }
    """
    if other_params is None:
        other_params = {}

    if not isinstance(property_list, list):
        property_list = [property_list]

    for k, prop in enumerate(property_list):
        tp = prop["type"]

        # ---------------------------------------------------------
        # Property: x[idx] >= rhs
        # ---------------------------------------------------------
        if tp == "x_ge":
            idx = int(prop["idx"])
            rhs = float(prop["rhs"])
            modelF.addConstr(xF[idx] >= rhs, name=f"prop_x_ge[{k},{idx}]")

        # ---------------------------------------------------------
        # Property: x[idx] <= rhs
        # ---------------------------------------------------------
        elif tp == "x_le":
            idx = int(prop["idx"])
            rhs = float(prop["rhs"])
            modelF.addConstr(xF[idx] <= rhs, name=f"prop_x_le[{k},{idx}]")

        # ---------------------------------------------------------
        # Property: sum_{j in idxs} x[j] >= rhs
        # ---------------------------------------------------------
        elif tp == "sum_ge":
            idxs = [int(i) for i in prop["idxs"]]
            rhs  = float(prop["rhs"])
            modelF.addConstr(gp.quicksum(xF[j] for j in idxs) >= rhs, name=f"prop_sum_ge[{k}]")

        # ---------------------------------------------------------
        # Property: sum_{j in idxs} x[j] <= rhs
        # ---------------------------------------------------------
        elif tp == "sum_le":
            idxs = [int(i) for i in prop["idxs"]]
            rhs  = float(prop["rhs"])
            modelF.addConstr(gp.quicksum(xF[j] for j in idxs) <= rhs, name=f"prop_sum_le[{k}]")

        # ---------------------------------------------------------
        # Custom user hook
        # ---------------------------------------------------------
        elif tp == "custom":
            # expr signature: expr(modelF, xF, other_params)
            prop["expr"](modelF, xF, other_params)

        else:
            raise ValueError(f"Unknown prop type: {tp}")

## Solo b mutable

In [6]:
def solve_relative_ce_mutable_b_only(c, A, b_hat, z_hat, alpha, b_bounds, favored_constraints):
    """
    Construct a relative CE with ONLY b mutable (within bounds).
    Variables:
        x >= 0
        b (mutable RHS within bounds)
    Objective:
        min ||b - b_hat||_1
    Constraints:
        A x >= b
        c^T x <= alpha * z_hat
        x in D(x_hat)  (favored_constraints)
        --------------
            Supported property types (examples):
      - {"type":"x_ge", "idx":0, "rhs":2.0}
      - [{"type":"x_le", "idx":1, "rhs":3.5} , {"type":"sum_ge", "idxs":[0,1], "rhs":7.0}]
      - {"type":"sum_le", "idxs":[0,1], "rhs":10.0}
      - {"type":"custom", "expr": lambda m,x,params: ... }
        -------------
        b in bounds
    Returns: x_ce, b_ce, cost_ce, l1_dev
    """
    m = gp.Model("relative_ce_mutable_b_only")
    m.Params.OutputFlag = 1  # set to 0 to silence

    n = len(c)
    m_con = len(b_hat)

    x = m.addVars(n, lb=0.0, name="x")
    b = m.addVars(m_con, lb=-GRB.INFINITY, name="b")

    # L1 abs deviations
    d = m.addVars(m_con, lb=0.0, name="d")

    # A x >= b
    for i in range(m_con):
        m.addConstr(gp.quicksum(A[i][j] * x[j] for j in range(n)) >= b[i], name=f"feas_{i}")

    # Relative cap: c^T x <= alpha * z_hat
    m.addConstr(gp.quicksum(c[j] * x[j] for j in range(n)) <= alpha * z_hat, name="relative_cap")

    # Favored constraints: linear constraints describing D(x_hat)
    apply_favorable_property(m, x, favored_constraints)


    # b bounds
    for i in range(m_con):
        lo, hi = b_bounds[i]
        m.addConstr(b[i] >= lo, name=f"b_lo_{i}")
        m.addConstr(b[i] <= hi, name=f"b_hi_{i}")

    # d_i >= |b_i - b_hat_i|
    for i in range(m_con):
        m.addConstr(d[i] >= b[i] - b_hat[i], name=f"abs_pos_{i}")
        m.addConstr(d[i] >= -(b[i] - b_hat[i]), name=f"abs_neg_{i}")

    # objective: min sum d_i
    m.setObjective(gp.quicksum(d[i] for i in range(m_con)), GRB.MINIMIZE)

    m.optimize()
    if m.Status != GRB.OPTIMAL:
        raise RuntimeError(f"Relative CE model not optimal. Status={m.Status}")

    x_ce = [x[j].X for j in range(n)]
    b_ce = [b[i].X for i in range(m_con)]
    cost_ce = sum(c[j] * x_ce[j] for j in range(n))
    l1_dev = m.ObjVal

    return x_ce, b_ce, cost_ce, l1_dev


def sanity_check_relative_ce(c, A, b_ce, favored_constraints, alpha, z_hat):
    """
    Verification step (sanity check):
    Solve:
        min c^T x
        s.t. A x >= b_ce
             x in D(x_hat) (favored_constraints)
             x >= 0
    Let z_tilde be optimal value. Pass if z_tilde <= alpha * z_hat.
    Returns: (is_valid, z_tilde, x_star)
    """
    m = gp.Model("sanity_check")
    m.Params.OutputFlag = 0

    n = len(c)
    m_con = len(b_ce)

    x = m.addVars(n, lb=0.0, name="x")

    m.setObjective(gp.quicksum(c[j] * x[j] for j in range(n)), GRB.MINIMIZE)

    for i in range(m_con):
        m.addConstr(gp.quicksum(A[i][j] * x[j] for j in range(n)) >= b_ce[i], name=f"feas_{i}")

    apply_favorable_property(m, x, favored_constraints)

    m.optimize()
    if m.Status != GRB.OPTIMAL:
        return False, None, None

    z_tilde = m.ObjVal
    x_star = [x[j].X for j in range(n)]

    # Numerical tolerance
    tol = 1e-6
    is_valid = z_tilde <= alpha * z_hat + tol

    return is_valid, z_tilde, x_star


def main():
    # -------------------
    # 1) Your instance
    # -------------------
    c = [3.0, 5.0]
    A = [
        [1.0, 2.0],
        [3.0, 2.0],
    ]
    b_hat = [10.0, 12.0]

    # -------------------
    # 2) Solve factual LP
    # -------------------
    x_hat, z_hat = solve_original_lp(c, A, b_hat)
    print("=== ORIGINAL (FACTUAL) ===")
    print("x_hat =", x_hat)
    print("z_hat =", z_hat)

    # -------------------
    # 3) Relative CE settings (baseline)
    # -------------------
    alpha = 0.9

    # Mutable b only within bounds
    b_bounds = [
        (9.0, 11.0),    # b1 in [9, 11]
        (11.0, 13.0),   # b2 in [11, 13]
    ]

    # Favored set D(x_hat): x1 >= 2
    # For solve_relative_ce_mutable_b_only (expects dicts for apply_favorable_property)
    favored_constraints = [{"type": "x_ge", "idx": 0, "rhs": x_hat[0] + 1.0}]


    # -------------------
    # 4) Solve Relative CE construction
    # -------------------
    x_ce, b_ce, cost_ce, l1_dev = solve_relative_ce_mutable_b_only(
        c=c, A=A, b_hat=b_hat, z_hat=z_hat, alpha=alpha,
        b_bounds=b_bounds, favored_constraints=favored_constraints
    )

    print("\n=== ORIGINAL (FACTUAL) ===")
    print("x_hat =", x_hat)
    print("z_hat =", z_hat)
    print("b_hat =", b_hat)


    print("\n=== RELATIVE CE (CONSTRUCTION) ===")
    print("alpha =", alpha)
    print("x_CE  =", x_ce)
    print("b_CE  =", b_ce)
    print("c^T x_CE =", cost_ce, "cap =", alpha * z_hat)
    print("Objective (L1) ||b - b_hat||_1 =", l1_dev)

    # -------------------
    # 5) Sanity check (verification)
    # -------------------
    valid, z_check, x_star = sanity_check_relative_ce(
        c=c, A=A, b_ce=b_ce, favored_constraints=favored_constraints_for_ce, # Changed to use dictionary format
        alpha=alpha, z_hat=z_hat
    )

    print("\n=== SANITY CHECK (VERIFICATION) ===")
    if z_check is None:
        print("Verification LP infeasible or not optimal -> NOT a valid relative CE.")
        return

    print("x_star (optimal under (c,A,b_CE) with D) =", x_star)
    print("z_check =", z_check)
    print("threshold alpha*z_hat =", alpha * z_hat)
    print("VALID relative CE? ->", valid)

    # Optional: enforce strict pipeline correctness
    if not valid:
        raise RuntimeError("Sanity check failed: constructed (c,A,b) is NOT a valid relative CE.")


if __name__ == "__main__":
    main()


Set parameter WLSAccessID
Set parameter WLSSecret
Set parameter LicenseID to value 2653481
Academic license 2653481 - for non-commercial use only - registered to to___@ug.uchile.cl
=== ORIGINAL (FACTUAL) ===
x_hat = [1.0000000000000007, 4.499999999999999]
z_hat = 25.5
Set parameter OutputFlag to value 1
Gurobi Optimizer version 13.0.0 build v13.0.0rc1 (win64 - Windows 11.0 (26100.2))

CPU model: 12th Gen Intel(R) Core(TM) i9-12900K, instruction set [SSE2|AVX|AVX2]
Thread count: 16 physical cores, 24 logical processors, using up to 24 threads

Academic license 2653481 - for non-commercial use only - registered to to___@ug.uchile.cl
Optimize a model with 12 rows, 6 columns and 21 nonzeros (Min)
Model fingerprint: 0x5113ff59
Model has 2 linear objective coefficients
Coefficient statistics:
  Matrix range     [1e+00, 5e+00]
  Objective range  [1e+00, 1e+00]
  Bounds range     [0e+00, 0e+00]
  RHS range        [2e+00, 2e+01]
Presolve removed 7 rows and 2 columns
Presolve time: 0.01s

Solved

RuntimeError: Relative CE model not optimal. Status=3

## A y b mutable

In [7]:
def solve_relative_ce_mutable_Ab(c, A_hat, b_hat, z_hat, alpha,
                                 A_bounds, b_bounds,
                                 favored_constraints, other_params=None,
                                 output=1):
    """
    Variables:
      x_j >= 0
      b_i (mutable RHS)
      u_{ij} = a_{ij} x_j  (scaled coefficients)

    Constraints:
      sum_j u_{ij} >= b_i                         (feasibility)
      c^T x <= alpha * z_hat                      (relative cap)
      x in D(x_hat) via foils
      b_i in [b_lo_i, b_hi_i]
      u_{ij} in [Alo_{ij} x_j, Ahi_{ij} x_j]      (encodes existence of A within bounds)

    Objective (LP):
      minimize  ||b - b_hat||_1  +  ||U - (A_hat * diag(x))||_1
      i.e. sum_i |b_i - b_hat_i| + sum_{i,j} |u_{ij} - A_hat_{ij} x_j|
    """
    if other_params is None:
        other_params = {}

    m = gp.Model("relative_ce_mutable_Ab")
    m.Params.OutputFlag = output

    m_con = len(b_hat)
    n = len(c)

    # Decision variables
    x = m.addVars(n, lb=0.0, name="x")
    b = m.addVars(m_con, lb=-GRB.INFINITY, name="b")
    u = m.addVars(m_con, n, lb=-GRB.INFINITY, name="u")  # u[i,j] = a_ij * x_j

    # Abs deviations (L1)
    db = m.addVars(m_con, lb=0.0, name="db")
    du = m.addVars(m_con, n, lb=0.0, name="du")

    # Feasibility: sum_j u_ij >= b_i
    for i in range(m_con):
        m.addConstr(gp.quicksum(u[i, j] for j in range(n)) >= b[i], name=f"feas_{i}")

    # Relative cap
    m.addConstr(gp.quicksum(c[j] * x[j] for j in range(n)) <= alpha * z_hat, name="relative_cap")

    # Favored set via foils
    apply_favorable_property(m, x, favored_constraints, other_params=other_params)

    # b bounds and |b - b_hat|
    for i in range(m_con):
        blo, bhi = b_bounds[i]
        m.addConstr(b[i] >= blo, name=f"b_lo_{i}")
        m.addConstr(b[i] <= bhi, name=f"b_hi_{i}")

        m.addConstr(db[i] >=  b[i] - b_hat[i], name=f"absb_pos_{i}")
        m.addConstr(db[i] >= -(b[i] - b_hat[i]), name=f"absb_neg_{i}")

    # U bounds encode existence of A within bounds:
    # Alo_ij * x_j <= u_ij <= Ahi_ij * x_j
    # Also define |u_ij - A_hat_ij x_j|
    for i in range(m_con):
        for j in range(n):
            Alo, Ahi = A_bounds[i][j]

            m.addConstr(u[i, j] >= Alo * x[j], name=f"u_lo[{i},{j}]")
            m.addConstr(u[i, j] <= Ahi * x[j], name=f"u_hi[{i},{j}]")

            # abs linearization around baseline scaled value A_hat_ij * x_j
            m.addConstr(du[i, j] >=  u[i, j] - A_hat[i][j] * x[j], name=f"absu_pos[{i},{j}]")
            m.addConstr(du[i, j] >= -(u[i, j] - A_hat[i][j] * x[j]), name=f"absu_neg[{i},{j}]")

    # Objective: min sum db + sum du
    m.setObjective(gp.quicksum(db[i] for i in range(m_con)) +
                   gp.quicksum(du[i, j] for i in range(m_con) for j in range(n)),
                   GRB.MINIMIZE)

    m.optimize()
    if m.Status != GRB.OPTIMAL:
        raise RuntimeError(f"Relative CE model not optimal. Status={m.Status}")

    x_ce = [x[j].X for j in range(n)]
    b_ce = [b[i].X for i in range(m_con)]
    u_ce = [[u[i, j].X for j in range(n)] for i in range(m_con)]

    z_ce = sum(c[j] * x_ce[j] for j in range(n))
    obj = m.ObjVal
    return x_ce, b_ce, u_ce, z_ce, obj

In [8]:
# Recover a concrete A_ce from (u_ce, x_ce) within bounds
# -----------------------------
def recover_A_from_u_x(u_ce, x_ce, A_bounds, A_fallback=None, eps=1e-8):
    m_con = len(u_ce)
    n = len(x_ce)

    A_ce = [[0.0 for _ in range(n)] for _ in range(m_con)]

    for i in range(m_con):
        for j in range(n):
            Alo, Ahi = A_bounds[i][j]
            if x_ce[j] > eps:
                val = u_ce[i][j] / x_ce[j]
                # clip for numerical safety
                val = max(Alo, min(Ahi, val))
                A_ce[i][j] = val
            else:
                # if x_j == 0, u_ij should be 0 due to bounds; choose any feasible coefficient
                if A_fallback is not None:
                    val = A_fallback[i][j]
                    A_ce[i][j] = max(Alo, min(Ahi, val))
                else:
                    A_ce[i][j] = Alo  # any feasible value
    return A_ce


# -----------------------------
# Sanity check: verify with fixed (A_ce, b_ce) and same foils
# -----------------------------
def sanity_check_relative_ce(c, A_ce, b_ce, favored_constraints, alpha, z_hat, other_params=None, output=0):
    if other_params is None:
        other_params = {}

    m = gp.Model("sanity_check")
    m.Params.OutputFlag = output

    n = len(c)
    m_con = len(b_ce)

    x = m.addVars(n, lb=0.0, name="x")
    m.setObjective(gp.quicksum(c[j] * x[j] for j in range(n)), GRB.MINIMIZE)

    for i in range(m_con):
        m.addConstr(gp.quicksum(A_ce[i][j] * x[j] for j in range(n)) >= b_ce[i], name=f"feas_{i}")

    apply_favorable_property(m, x, favored_constraints, other_params=other_params)

    m.optimize()
    if m.Status != GRB.OPTIMAL:
        return False, None, None

    z_star = m.ObjVal
    x_star = [x[j].X for j in range(n)]
    valid = (z_star <= alpha * z_hat + 1e-6)
    return valid, z_star, x_star



In [9]:
if __name__ == "__main__":
    # Data
    c = [3.0, 5.0]
    A_hat = [
        [1.0, 2.0],
        [3.0, 2.0],
    ]
    b_hat = [10.0, 12.0]

    # 1) Factual solve
    x_hat, z_hat = solve_original_lp(c, A_hat, b_hat, output=0)
    print("=== FACTUAL ===")
    print("x_hat =", x_hat)
    print("z_hat =", z_hat)

    # 2) Choose alpha
    alpha = 0.9

    # 3) Foils (favored set): example x1 >= x_hat1 + 1
    favored_constraints = [{"type": "x_ge", "idx": 0, "rhs": x_hat[0] + 1.0}]
    other_params = {"x_hat": x_hat, "z_hat": z_hat}

    # 4) Bounds for b (mutable RHS)
    b_bounds = [
        (9.0, 11.0),
        (11.0, 13.0),
    ]

    # 5) Bounds for A (mutable coefficients) — example: ±10% box around A_hat
    #    You can tighten/relax these as you like.
    A_bounds = []
    for i in range(len(A_hat)):
        row = []
        for j in range(len(A_hat[0])):
            base = A_hat[i][j]
            lo = 0.90 * base
            hi = 1.10 * base
            row.append((lo, hi))
        A_bounds.append(row)

    # 6) Construct Relative CE with mutable A and b
    x_ce, b_ce, u_ce, z_ce, obj = solve_relative_ce_mutable_Ab(
        c=c, A_hat=A_hat, b_hat=b_hat, z_hat=z_hat, alpha=alpha,
        A_bounds=A_bounds, b_bounds=b_bounds,
        favored_constraints=favored_constraints, other_params=other_params,
        output=1
    )


    print("\n=== FACTUAL ===")
    print("x_hat =", x_hat)
    print("z_hat =", z_hat)
    print("b_hat =", b_hat)
    print("A_hat =", A_hat)

    print("\n=== RELATIVE CE (CONSTRUCTION) ===")
    print("x_ce =", x_ce)
    print("b_ce =", b_ce)
    print("z_ce =", z_ce, "cap =", alpha * z_hat)
    print("objective (L1 in b and U) =", obj)

    # 7) Recover a concrete A_ce from (u_ce, x_ce)
    A_ce = recover_A_from_u_x(u_ce, x_ce, A_bounds, A_fallback=A_hat)

    # 8) Sanity check on induced instance (A_ce, b_ce)
    valid, z_star, x_star = sanity_check_relative_ce(
        c=c, A_ce=A_ce, b_ce=b_ce, favored_constraints=favored_constraints,
        alpha=alpha, z_hat=z_hat, other_params=other_params, output=0
    )

    print("\n=== SANITY CHECK ===")
    print("A_ce =", A_ce)
    print("x_star =", x_star)
    print("z_star =", z_star)
    print("threshold =", alpha * z_hat)
    print("VALID? ->", valid)

    if not valid:
        raise RuntimeError("Sanity check failed: candidate (A_ce, b_ce) is NOT a valid relative CE.")


=== FACTUAL ===
x_hat = [1.0000000000000007, 4.499999999999999]
z_hat = 25.5
Set parameter OutputFlag to value 1
Gurobi Optimizer version 13.0.0 build v13.0.0rc1 (win64 - Windows 11.0 (26100.2))

CPU model: 12th Gen Intel(R) Core(TM) i9-12900K, instruction set [SSE2|AVX|AVX2]
Thread count: 16 physical cores, 24 logical processors, using up to 24 threads

Academic license 2653481 - for non-commercial use only - registered to to___@ug.uchile.cl
Optimize a model with 28 rows, 14 columns and 61 nonzeros (Min)
Model fingerprint: 0x22f6725c
Model has 6 linear objective coefficients
Coefficient statistics:
  Matrix range     [9e-01, 5e+00]
  Objective range  [1e+00, 1e+00]
  Bounds range     [0e+00, 0e+00]
  RHS range        [2e+00, 2e+01]
Presolve removed 11 rows and 0 columns
Presolve time: 0.00s
Presolved: 17 rows, 14 columns, 54 nonzeros

Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    3.4065800e-01   2.406336e+00   0.000000e+00      0s
       9    1.2200000e+0

## c, A y b mutables

In [10]:
def solve_relative_ce_mutable_cAb(
    c_hat, A_hat, b_hat, z_hat, alpha,
    c_bounds, A_bounds, b_bounds,
    favored_constraints, other_params=None,
    output=1
):
    """
    Variables:
      x_j >= 0
      b_i
      w_j = c_j x_j
      u_{ij} = a_{ij} x_j

    Constraints:
      sum_j u_{ij} >= b_i                         (feasibility)
      sum_j w_j <= alpha * z_hat                  (relative cap on objective value)
      x in D(x_hat) via foils
      b_i in [blo_i, bhi_i]
      clo_j*x_j <= w_j <= chi_j*x_j               (encodes c in bounds)
      Alo_ij*x_j <= u_ij <= Ahi_ij*x_j            (encodes A in bounds)

    Objective (LP):
      minimize  ||b - b_hat||_1
              + ||w - (c_hat ∘ x)||_1
              + ||u - (A_hat * diag(x))||_1
    """
    if other_params is None:
        other_params = {}

    m = gp.Model("relative_ce_mutable_cAb")
    m.Params.OutputFlag = output

    m_con = len(b_hat)
    n = len(c_hat)

    # Decision variables
    x = m.addVars(n, lb=0.0, name="x")
    b = m.addVars(m_con, lb=-GRB.INFINITY, name="b")
    w = m.addVars(n, lb=-GRB.INFINITY, name="w")          # w_j = c_j x_j
    u = m.addVars(m_con, n, lb=-GRB.INFINITY, name="u")   # u_ij = a_ij x_j

    # L1 abs deviations
    db = m.addVars(m_con, lb=0.0, name="db")
    dw = m.addVars(n, lb=0.0, name="dw")
    du = m.addVars(m_con, n, lb=0.0, name="du")

    # Feasibility: U*1 >= b
    for i in range(m_con):
        m.addConstr(gp.quicksum(u[i, j] for j in range(n)) >= b[i], name=f"feas_{i}")

    # Relative cap: 1^T w <= alpha * z_hat
    m.addConstr(gp.quicksum(w[j] for j in range(n)) <= alpha * z_hat, name="relative_cap")

    # Favored set via foils
    apply_favorable_property(m, x, favored_constraints, other_params=other_params)

    # b bounds + |b - b_hat|
    for i in range(m_con):
        blo, bhi = b_bounds[i]
        m.addConstr(b[i] >= blo, name=f"b_lo_{i}")
        m.addConstr(b[i] <= bhi, name=f"b_hi_{i}")

        m.addConstr(db[i] >=  b[i] - b_hat[i], name=f"absb_pos_{i}")
        m.addConstr(db[i] >= -(b[i] - b_hat[i]), name=f"absb_neg_{i}")

    # c bounds encoded via w bounds + |w - c_hat*x|
    for j in range(n):
        clo, chi = c_bounds[j]
        m.addConstr(w[j] >= clo * x[j], name=f"w_lo_{j}")
        m.addConstr(w[j] <= chi * x[j], name=f"w_hi_{j}")

        m.addConstr(dw[j] >=  w[j] - c_hat[j] * x[j], name=f"absw_pos_{j}")
        m.addConstr(dw[j] >= -(w[j] - c_hat[j] * x[j]), name=f"absw_neg_{j}")

    # A bounds encoded via u bounds + |u - A_hat*x|
    for i in range(m_con):
        for j in range(n):
            Alo, Ahi = A_bounds[i][j]
            m.addConstr(u[i, j] >= Alo * x[j], name=f"u_lo[{i},{j}]")
            m.addConstr(u[i, j] <= Ahi * x[j], name=f"u_hi[{i},{j}]")

            m.addConstr(du[i, j] >=  u[i, j] - A_hat[i][j] * x[j], name=f"absu_pos[{i},{j}]")
            m.addConstr(du[i, j] >= -(u[i, j] - A_hat[i][j] * x[j]), name=f"absu_neg[{i},{j}]")

    # Objective
    m.setObjective(
        gp.quicksum(db[i] for i in range(m_con)) +
        gp.quicksum(dw[j] for j in range(n)) +
        gp.quicksum(du[i, j] for i in range(m_con) for j in range(n)),
        GRB.MINIMIZE
    )

    m.optimize()
    if m.Status != GRB.OPTIMAL:
        raise RuntimeError(f"Relative CE model not optimal. Status={m.Status}")

    x_ce = [x[j].X for j in range(n)]
    b_ce = [b[i].X for i in range(m_con)]
    w_ce = [w[j].X for j in range(n)]
    u_ce = [[u[i, j].X for j in range(n)] for i in range(m_con)]
    obj = m.ObjVal

    return x_ce, b_ce, w_ce, u_ce, obj


In [11]:
# -----------------------------
# Recover concrete c_ce and A_ce from (w_ce, u_ce, x_ce)
# -----------------------------
def recover_cA_from_wu_x(w_ce, u_ce, x_ce, c_bounds, A_bounds, c_fallback=None, A_fallback=None, eps=1e-8):
    m_con = len(u_ce)
    n = len(x_ce)

    c_ce = [0.0] * n
    A_ce = [[0.0 for _ in range(n)] for _ in range(m_con)]

    for j in range(n):
        clo, chi = c_bounds[j]
        if x_ce[j] > eps:
            val = w_ce[j] / x_ce[j]
            c_ce[j] = max(clo, min(chi, val))
        else:
            base = c_fallback[j] if c_fallback is not None else clo
            c_ce[j] = max(clo, min(chi, base))

    for i in range(m_con):
        for j in range(n):
            Alo, Ahi = A_bounds[i][j]
            if x_ce[j] > eps:
                val = u_ce[i][j] / x_ce[j]
                A_ce[i][j] = max(Alo, min(Ahi, val))
            else:
                base = A_fallback[i][j] if A_fallback is not None else Alo
                A_ce[i][j] = max(Alo, min(Ahi, base))

    return c_ce, A_ce

In [12]:
def sanity_check_relative_ce(c_ce, A_ce, b_ce, favored_constraints, alpha, z_hat, other_params=None, output=0):
    if other_params is None:
        other_params = {}

    m = gp.Model("sanity_check")
    m.Params.OutputFlag = output

    n = len(c_ce)
    m_con = len(b_ce)

    x = m.addVars(n, lb=0.0, name="x")
    m.setObjective(gp.quicksum(c_ce[j] * x[j] for j in range(n)), GRB.MINIMIZE)

    for i in range(m_con):
        m.addConstr(gp.quicksum(A_ce[i][j] * x[j] for j in range(n)) >= b_ce[i], name=f"feas_{i}")

    apply_favorable_property(m, x, favored_constraints, other_params=other_params)

    m.optimize()
    if m.Status != GRB.OPTIMAL:
        return False, None, None

    z_star = m.ObjVal
    x_star = [x[j].X for j in range(n)]
    valid = (z_star <= alpha * z_hat + 1e-6)
    return valid, z_star, x_star

In [13]:
if __name__ == "__main__":
    c_hat = [3.0, 5.0]
    A_hat = [
        [1.0, 2.0],
        [3.0, 2.0],
    ]
    b_hat = [10.0, 12.0]

    # 1) factual solve
    x_hat, z_hat = solve_original_lp(c_hat, A_hat, b_hat, output=0)
    print("=== FACTUAL ===")
    print("x_hat =", x_hat)
    print("z_hat =", z_hat)

    # 2) choose alpha
    alpha = 0.9

    # 3) foils (favored set) as function of x_hat
    # Example: force x1 >= x_hat1 + 1
    favored_constraints = [{"type": "x_ge", "idx": 0, "rhs": x_hat[0] + 1.0}]
    other_params = {"x_hat": x_hat, "z_hat": z_hat}

    # 4) bounds for b (mutable)
    b_bounds = [
        (9.0, 11.0),
        (11.0, 13.0),
    ]

    # 5) bounds for c (mutable) — example: ±10%
    c_bounds = []
    for j in range(len(c_hat)):
        c_bounds.append((0.90 * c_hat[j], 1.10 * c_hat[j]))

    # 6) bounds for A (mutable) — example: ±10%
    A_bounds = []
    for i in range(len(A_hat)):
        row = []
        for j in range(len(A_hat[0])):
            row.append((0.90 * A_hat[i][j], 1.10 * A_hat[i][j]))
        A_bounds.append(row)

    # 7) construct relative CE
    x_ce, b_ce, w_ce, u_ce, obj = solve_relative_ce_mutable_cAb(
        c_hat=c_hat, A_hat=A_hat, b_hat=b_hat, z_hat=z_hat, alpha=alpha,
        c_bounds=c_bounds, A_bounds=A_bounds, b_bounds=b_bounds,
        favored_constraints=favored_constraints, other_params=other_params,
        output=1
    )

    print("\n=== FACTUAL ===")
    print("x_hat =", x_hat)
    print("z_hat =", z_hat)
    print("b_hat =", b_hat)
    print("A_hat =", A_hat)

    print("\n=== RELATIVE CE (CONSTRUCTION) ===")
    print("x_ce =", x_ce)
    print("b_ce =", b_ce)
    print("w_ce =", w_ce)
    print("objective (L1) =", obj)
    print("cap alpha*z_hat =", alpha * z_hat, "   1^T w_ce =", sum(w_ce))

    # 8) recover concrete (c_ce, A_ce)
    c_ce, A_ce = recover_cA_from_wu_x(
        w_ce=w_ce, u_ce=u_ce, x_ce=x_ce,
        c_bounds=c_bounds, A_bounds=A_bounds,
        c_fallback=c_hat, A_fallback=A_hat
    )

    # 9) sanity check
    valid, z_star, x_star = sanity_check_relative_ce(
        c_ce=c_ce, A_ce=A_ce, b_ce=b_ce,
        favored_constraints=favored_constraints,
        alpha=alpha, z_hat=z_hat,
        other_params=other_params,
        output=0
    )

    print("\n=== SANITY CHECK ===")
    print("c_ce =", c_ce)
    print("A_ce =", A_ce)
    print("x_star =", x_star)
    print("z_star =", z_star)
    print("threshold =", alpha * z_hat)
    print("VALID? ->", valid)

    if not valid:
        raise RuntimeError("Sanity check failed: reconstructed (c_ce, A_ce, b_ce) is NOT a valid relative CE.")


=== FACTUAL ===
x_hat = [1.0000000000000007, 4.499999999999999]
z_hat = 25.5
Set parameter OutputFlag to value 1
Gurobi Optimizer version 13.0.0 build v13.0.0rc1 (win64 - Windows 11.0 (26100.2))

CPU model: 12th Gen Intel(R) Core(TM) i9-12900K, instruction set [SSE2|AVX|AVX2]
Thread count: 16 physical cores, 24 logical processors, using up to 24 threads

Academic license 2653481 - for non-commercial use only - registered to to___@ug.uchile.cl
Optimize a model with 36 rows, 18 columns and 81 nonzeros (Min)
Model fingerprint: 0x293bd014
Model has 8 linear objective coefficients
Coefficient statistics:
  Matrix range     [9e-01, 6e+00]
  Objective range  [1e+00, 1e+00]
  Bounds range     [0e+00, 0e+00]
  RHS range        [2e+00, 2e+01]
Presolve removed 11 rows and 0 columns
Presolve time: 0.00s
Presolved: 25 rows, 18 columns, 76 nonzeros

Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    0.0000000e+00   7.412500e+00   0.000000e+00      0s
      14    1.2200000e+0

## Problemas màs grandes

In [14]:
import random


def generate_ce_instance_bundle(
    m_con: int,
    n_var: int,
    seed: int = 7,
    # cómo generar instancia original
    A_max: float = 5.0,
    c_min: float = 1.0,
    c_max: float = 10.0,
    x_feas_min: float = 1.0,
    x_feas_max: float = 5.0,
    slack_min: float = 0.5,
    slack_max: float = 3.0,
    # bounds CE (porcentuales)
    pct_c: float = 0.10,     # ±10% para c
    pct_A: float = 0.10,     # ±10% para A
    pct_b: float = 0.10,     # ±10% para b
    b_delta_floor: float = 0.5,  # mínimo ancho para bounds de b
    # foils (se construyen como "plantillas" y luego se concretan con x_hat)
    foil_mode: str = "increase_top1",   # "increase_top1" | "increase_topk" | "sum_ge"
    foil_strength: float = 1.25,        # multiplicador sobre x_hat (1.25 => +25%)
    foil_k: int = 3,                    # usado si foil_mode == "increase_topk"
    foil_sum_size: int = 5,             # usado si foil_mode == "sum_ge"
    foil_sum_factor: float = 1.10       # rhs = factor * sum(x_hat[idxs])
):
    """
    Retorna un dict con:
      - c_hat, A_hat, b_hat
      - c_bounds, A_bounds, b_bounds
      - foil_template: dict que describe cómo construir foil_list una vez que se conoce x_hat
      - meta: info útil (seed, tamaños, etc.)
    """

    rng = random.Random(seed)

    # 1) Generar instancia original factible (A>=0, c>0, x_feas>0)
    c_hat = [rng.uniform(c_min, c_max) for _ in range(n_var)]
    A_hat = [[rng.uniform(0.0, A_max) for _ in range(n_var)] for _ in range(m_con)]
    x_feas = [rng.uniform(x_feas_min, x_feas_max) for _ in range(n_var)]
    slack = [rng.uniform(slack_min, slack_max) for _ in range(m_con)]

    # b_hat = A_hat x_feas - slack  => A_hat x_feas >= b_hat
    b_hat = []
    for i in range(m_con):
        Ax = sum(A_hat[i][j] * x_feas[j] for j in range(n_var))
        b_hat.append(Ax - slack[i])

    # 2) Bounds para c (box)
    c_bounds = []
    for j in range(n_var):
        base = c_hat[j]
        c_bounds.append(((1.0 - pct_c) * base, (1.0 + pct_c) * base))

    # 3) Bounds para A (box por entrada)
    A_bounds = []
    for i in range(m_con):
        row = []
        for j in range(n_var):
            base = A_hat[i][j]
            row.append(((1.0 - pct_A) * base, (1.0 + pct_A) * base))
        A_bounds.append(row)

    # 4) Bounds para b (box por componente)
    b_bounds = []
    for i in range(m_con):
        base = abs(b_hat[i])
        delta = max(b_delta_floor, pct_b * base)
        b_bounds.append((b_hat[i] - delta, b_hat[i] + delta))

    # 5) Plantilla para construir foils después de resolver el factual (cuando tengas x_hat)
    foil_template = {
        "mode": foil_mode,
        "strength": foil_strength,
        "k": foil_k,
        "sum_size": foil_sum_size,
        "sum_factor": foil_sum_factor,
    }

    return {
        "c_hat": c_hat,
        "A_hat": A_hat,
        "b_hat": b_hat,
        "c_bounds": c_bounds,
        "A_bounds": A_bounds,
        "b_bounds": b_bounds,
        "foil_template": foil_template,
        "meta": {"m_con": m_con, "n_var": n_var, "seed": seed}
    }

In [15]:
def build_foil_list_from_template(x_hat, foil_template):
    mode = foil_template["mode"]

    if mode == "increase_top1":
        j_star = max(range(len(x_hat)), key=lambda j: x_hat[j])
        return [{"type": "x_ge", "idx": j_star, "rhs": foil_template["strength"] * x_hat[j_star]}]

    if mode == "increase_topk":
        k = int(foil_template["k"])
        idxs = sorted(range(len(x_hat)), key=lambda j: x_hat[j], reverse=True)[:k]
        return [{"type": "x_ge", "idx": j, "rhs": foil_template["strength"] * x_hat[j]} for j in idxs]

    if mode == "sum_ge":
        s = int(foil_template["sum_size"])
        # toma las s variables con mayor x_hat
        idxs = sorted(range(len(x_hat)), key=lambda j: x_hat[j], reverse=True)[:s]
        rhs = foil_template["sum_factor"] * sum(x_hat[j] for j in idxs)
        return [{"type": "sum_ge", "idxs": idxs, "rhs": rhs}]

    raise ValueError(f"Unknown foil mode: {mode}")


In [16]:
# 1) Genera instancia grande + bounds + plantilla
bundle = generate_ce_instance_bundle(m_con=300, n_var=800, seed=11)

c_hat = bundle["c_hat"]
A_hat = bundle["A_hat"]
b_hat = bundle["b_hat"]

c_bounds = bundle["c_bounds"]
A_bounds = bundle["A_bounds"]
b_bounds = bundle["b_bounds"]

# 2) Resuelve factual (usa tu función existente)
x_hat, z_hat = solve_original_lp(c_hat, A_hat, b_hat, output=0)

# 3) Construye foils en función de x_hat
foil_list = build_foil_list_from_template(x_hat, bundle["foil_template"])
other_params = {"x_hat": x_hat, "z_hat": z_hat}

# 4) Define alpha
alpha = 0.990

# 5) Construcción CE (usa tu solve_relative_ce_mutable_cAb)
x_ce, b_ce, w_ce, u_ce, obj = solve_relative_ce_mutable_cAb(
    c_hat=c_hat, A_hat=A_hat, b_hat=b_hat, z_hat=z_hat, alpha=alpha,
    c_bounds=c_bounds, A_bounds=A_bounds, b_bounds=b_bounds,
    favored_constraints=foil_list, other_params=other_params,
    output=1
)

# 6) Reconstruye (c_ce, A_ce)
c_ce, A_ce = recover_cA_from_wu_x(
    w_ce=w_ce, u_ce=u_ce, x_ce=x_ce,
    c_bounds=c_bounds, A_bounds=A_bounds,
    c_fallback=c_hat, A_fallback=A_hat
)

# 7) Sanity check
valid, z_star, x_star = sanity_check_relative_ce(
    c_ce=c_ce, A_ce=A_ce, b_ce=b_ce,
    favored_constraints=foil_list, alpha=alpha, z_hat=z_hat,
    other_params=other_params, output=0
)
print("VALID CE?", valid, " z_star=", z_star, " threshold=", alpha*z_hat)


Set parameter OutputFlag to value 1
Gurobi Optimizer version 13.0.0 build v13.0.0rc1 (win64 - Windows 11.0 (26100.2))

CPU model: 12th Gen Intel(R) Core(TM) i9-12900K, instruction set [SSE2|AVX|AVX2]
Thread count: 16 physical cores, 24 logical processors, using up to 24 threads

Academic license 2653481 - for non-commercial use only - registered to to___@ug.uchile.cl
Optimize a model with 964702 rows, 483000 columns and 2650901 nonzeros (Min)
Model fingerprint: 0x6b0e2023
Model has 241100 linear objective coefficients
Coefficient statistics:
  Matrix range     [7e-06, 1e+01]
  Objective range  [1e+00, 1e+00]
  Bounds range     [0e+00, 0e+00]
  RHS range        [2e+02, 7e+03]
Presolve removed 196642 rows and 0 columns (presolve time = 5s)...
Presolve removed 241401 rows and 0 columns
Presolve time: 7.75s
Presolved: 723301 rows, 483000 columns, 2409500 nonzeros

Concurrent LP optimizer: primal simplex, dual simplex, and barrier
Showing barrier log only...

Ordering time: 0.38s

Barrier s

In [ ]:
print("=== FACTUAL ===")
print("x_hat =", x_hat)
print("z_hat =", z_hat)
print("b_hat =", b_hat)
print("A_hat =", A_hat)

print("\n=== RELATIVE CE (CONSTRUCTION) ===")
print("x_ce =", x_ce)
print("b_ce =", b_ce)
print("w_ce =", w_ce)
print("objective (L1) =", obj)


=== FACTUAL ===
x_hat = [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 12.237723177084765, 0.0, 0.0, 0.0, 0.0, 0.0, 78.62689232559718, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 5.5096508266028925, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 52.55302806235729, 0.0, 0.0, 0.0, 0.0, 0.0, 85.03095265084012, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 138.40965019593077, 0.0, 0.0, 17.885801836785383, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 181.47087896578367, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0